In [1]:
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib import animation
from matplotlib.colors import Normalize, to_rgb
from mpl_toolkits.mplot3d import Axes3D
from scipy.special import lambertw
from scipy.special import gamma
from PIL import Image
from functools import reduce
from PsiPlot import *
from IPython.display import display

mpl.rcParams['figure.dpi'] = 100
mpl.rcParams['text.usetex'] = True
mpl.rcParams['text.latex.preamble'] = r'\usepackage{amsmath,amsfonts,physics}'
mpl.rcParams["animation.html"] = "jshtml"

%matplotlib inline

In all calculations, $m$ and $\hbar$ are assumed to be 1.

In [2]:
def Superpos_Period(energy_func, qn, param={}, epsilon=1e-5):
    def gcd(a, b):
        while b > epsilon:
            t, b = b, a % b
            a = t
        return a
    def gcd_list(ls):
        return reduce(gcd, ls)
    
    qn = np.asarray(qn)
    energies = energy_func(qn[...,0], qn[...,1], **param)
    energy_gcd = gcd_list(energies)
    return 2 * np.pi / energy_gcd

In [3]:
# Attempt to test the free-particle to ISW transform
def Free_to_ISW(x, t, freeWave, L=1, jmax=1000):
    return sum([freeWave(x + 2*i*L, t) - freeWave(x - 2*i*L, t) for i in range(-jmax, jmax+1)])

In [4]:
def Make_Axis_Labels(x_range, y_range, acc, num_labels):
    # Stole this from a stack exchange post...gonna have to find that...
    nx = int(np.abs(x_range[1] - x_range[0]) / acc)
    ny = int(np.abs(y_range[1] - y_range[0]) / acc)
    xs = np.linspace(*x_range, nx)
    ys = np.flip(np.linspace(*y_range, ny))
    step_x = int(nx / (num_labels - 1)) # step between consecutive labels
    step_y = int(ny / (num_labels - 1))
    x_positions = np.append(np.arange(0,nx,step_x), nx-1) # pixel count at label position
    y_positions = np.append(np.arange(0,ny,step_y), ny-1)
    x_labels = ["{:.2f}".format(a) for a in np.append(xs[::step_x], xs[-1])] # labels you want to see
    y_labels = ["{:.2f}".format(a) for a in np.append(ys[::step_y], ys[-1])]
    return x_labels, x_positions, y_labels, y_positions

# Plot 1D wavefunction
# Args
## wavefunc: a complex function of x and t
## x_range:  the range of x values to plot
## acc:      the accuracy to use
## options:  various plotting options:
###     -cmap:    the colormap to use for phase (default is hsv)
###     -y_range: the range of y values to plot (default is max produced by function over the x_range)
###     -title:   the title to use for the graph
###     -xlabel: the x-axis label
###     -ylabel: the y-axis label
def Plot_Wavefunction_1D(wavefunc, x_range, acc, options={}):
    x_range = np.array(x_range)
    n_sample = int((x_range[1]-x_range[0])/acc)
    x = np.linspace(x_range[0], x_range[1], n_sample)
    y = np.abs(wavefunc(x))
    z = ((np.angle(wavefunc(x)) + 2*np.pi) % (2 * np.pi))
    cmap = options["cmap"] if "cmap" in options else cm.hsv
    if "y_range" in options:
        plt.ylim(*options["y_range"])
    if "title" in options:
        plt.title(options["title"])
    if "xlabel" in options:
        plt.xlabel(options["xlabel"])
    if "ylabel" in options:
        plt.ylabel(options["ylabel"])
    if "colorbar" in options and options["colorbar"]:
        norm = Normalize(vmin=0, vmax=2*np.pi)
        plt.colorbar(cm.ScalarMappable(norm=norm,cmap=cmap), label=r"$\arg(\Psi)$", ax=plt.gca())
    #plt.plot(x, y)
    for i in range(n_sample-1):
        plt.fill_between([x[i], x[i+1]], [y[i], y[i+1]], color=cmap(z[i]/(2*np.pi)))
        
# Plot 2D Image of a 2D Wavefunction
# Args:
## wavefunc: a complex function of x, y and t
## x_range:  the range of x values to plot
## y_range:  the range of y values to plot
## acc:      the accuracy to use
## options:  various plotting options:
###     -cmap:    the color map to use for phase
###     -title:   the title to use for the graph
###     -axis-on: True iff the axis should be on
# getting axis labels while using imshow: https://stackoverflow.com/questions/18696122/change-values-on-matplotlib-imshow-graph-axis
def Plot_Wavefunction_2D_Image(wavefunc, x_range, y_range, acc, options={}, norm=None):
    x_range = np.array(x_range)
    y_range = np.array(y_range)
    X,Y = np.mgrid[x_range[0]:x_range[1]:acc, y_range[0]:y_range[1]:acc]
    vals = wavefunc(X,Y)
    mag = np.abs(vals)
    norm = mag.max() if norm is None else norm
    mag = mag / norm
    phase = (np.angle(vals) + np.pi) / (2 * np.pi)
    cmap = options["cmap"] if "cmap" in options else cm.hsv
    arr = cmap(phase)
    arr = np.insert(arr[:,:,:3], 3, mag, axis=2)
    plt.clf()
    # make axis labels
    x_labels, x_positions, y_labels, y_positions = Make_Axis_Labels(x_range, y_range, acc, 5)
    plt.xticks(x_positions, x_labels)
    plt.yticks(y_positions, y_labels)
    if not ("axis-on" in options) or not options["axis-on"]:
        plt.axis('off')
    if "title" in options:
        plt.title(options["title"])
    if "xlabel" in options:
        plt.xlabel(options["xlabel"])
    if "ylabel" in options:
        plt.ylabel(options["ylabel"])
    if "colorbar" in options and options["colorbar"]:
        norm = Normalize(vmin=0, vmax=2)
        plt.colorbar(cm.ScalarMappable(norm=norm,cmap=cmap), label=r"$\arg(\Psi)$")
    plt.imshow(arr)
    
def Plot_Wavefunction_2D_Graph(wavefunc, x_range, y_range, acc, options={}):
    x_range = np.array(x_range)
    y_range = np.array(y_range)
    x = np.arange(*x_range, acc)
    y = np.arange(*y_range, acc)
    X,Y = np.meshgrid(x,y)
    vals = wavefunc(X,Y)
    Z = np.abs(vals)
    phase = (np.angle(vals) + np.pi) / (2 * np.pi)
    cmap = options["cmap"] if "cmap" in options else cm.hsv
    norm = Normalize(vmin=0, vmax=2)
    m = cm.ScalarMappable(norm=norm, cmap=cmap)
    m.set_array([])
    fcolors = m.to_rgba(phase)
    plt.clf()
    fig = plt.figure()
    ax = fig.gca(projection='3d')
    ax.plot_surface(X,Y,Z, rstride=1, cstride=1, facecolors=fcolors, shade=False)
    
def Plot_Wavefunction_2D_Image_on_axis(wavefunc, x_range, y_range, acc, options, axis, norm=None):
    # Clear axis
    axis.clear()
    
    # Genrate x-y points
    X,Y = np.mgrid[x_range[0]:x_range[1]:acc, y_range[0]:y_range[1]:acc]
    
    # Evaluate wavefunction
    vals = wavefunc(X,Y)
    
    # Get magnitude for each sample point, then normalize
    mag = np.abs(vals)
    mag = mag / np.amax(mag)
    
    # Get the phases for each sample point, convert to color using cmap
    phase = (np.angle(vals) + np.pi) / (2 * np.pi)
    cmap = options["cmap"] if "cmap" in options else cm.hsv
    arr = cmap(phase)
    # Set the alpha channel for each sample to the normalized magnitude
    arr = np.insert(arr[:,:,:3], 3, mag, axis=2)
    
    ## Plot options
    if "axis-on" in options and options["axis-on"]:
        print("AXIS IS ON")
        x_labels, x_positions, y_labels, y_positions = Make_Axis_Labels(x_range, y_range, acc, options["num_labels"])
        if "xlabel-on" in options and options["xlabel-on"]:
            axis.set_xticks(x_positions)
            axis.set_xticklabels(x_labels)
        if "ylabel-on" in options and options["ylabel-on"]:
            axis.set_yticks(y_positions)
            axis.set_yticklabels(y_labels)
    else:
        axis.axis('off')
    if "title" in options:
        axis.set_title(options["title"])
    
    # Plot data
    axis.imshow(arr)
              
def Plot_Wavefunction_2D_Images(wavefuncs, x_ranges, y_ranges, accs, shape, axis_options, axarr):
    rows, cols = shape
    for r in range(rows):
        for c in range(cols):
            Plot_Wavefunction_2D_Image_on_axis(wavefuncs[r,c], x_ranges[r,c], y_ranges[r,c], accs[r,c], axis_options[r,c], axarr[r,c])


In [5]:
def Wavefunction_Animation_1D(f, acc, x_range, t_range, frames, plot_options={}):
    xs = np.arange(*x_range, acc)
    ts = np.linspace(*t_range, frames, endpoint=True)
    max_f = max([np.abs(f(x, t)) for x in xs for t in ts])
    plot_options["y_range"] = [0, 1.1*max_f]
    def animf(i):
        plt.clf()
        g = lambda x: f(x, ts[i])
        Plot_Wavefunction_1D(g, x_range, acc, plot_options)
        
    fig = plt.figure()
    return animation.FuncAnimation(fig, animf, frames=frames)
    
def Wavefunction_Animation_2D_Image(f, acc, x_range, y_range, t_range, plot_options, anim_options):
    fname = anim_options["filename"]
    frames = anim_options["frames"]
    fps = anim_options["fps"]
    dpi = anim_options["dpi"]
    norm_by_frame = plot_options["norm_by_frame"]
    ts = np.linspace(*t_range, frames, endpoint=False)
    
    if not norm_by_frame:
        print("Calculating global norm...")
        X,Y = np.mgrid[x_range[0]:x_range[1]:acc, y_range[0]:y_range[1]:acc]
        norm = np.max([np.abs(f(X,Y,t)) for t in ts])
    
    figsize = (plot_options["figsize-factor"], plot_options["figsize-factor"])
    fig, ax = plt.subplots(figsize=figsize)
    
    def animf(i):
        print("Frame: ", i)
        g = lambda x,y: f(x, y, ts[i])
        Plot_Wavefunction_2D_Image_on_axis(g, x_range, y_range, acc, plot_options, ax, (norm if not norm_by_frame else None))
        
    print("Begining frame compilation...")
    anim = animation.FuncAnimation(fig, animf, frames=frames)
    anim.save(fname, fps=fps, dpi=200)
    
                    
"""    
graph_options = {"accs": None,
                 "x_ranges": None,
                 "y_ranges": None,
                 "t_ranges": None
}
plot_options = {"shape": None,
                "colormap": cm.hsv,
                "figsize-factor":4,
                "sharex": False,
                "colorbar-on":False
}
axis_options = {"title": "",
                "axis-on": False,
                "xlabel-on": False,
                "ylabel-on":False,
                "num_labels": 5
}
anim_options = {"frames": 120,
                "fps": 30,
                "filename": "foo.mp4",
                "dpi": 200
} """
#if "colorbar" in options and options["colorbar"]:
        #norm = Normalize(vmin=0, vmax=2)
        #plt.colorbar(cm.ScalarMappable(norm=norm,cmap=cmap), label=r"$\arg(\Psi)\:mod\:\pi$")
def Wavefunction_Animation_2D_Images(funcs, graph_options, plot_options, axis_options, anim_options):
    # Ensure numpy arrays
    shape = np.asarray(plot_options["shape"])
    axis_options = np.reshape(np.asarray(axis_options), shape)
    funcs = np.reshape(np.asarray(funcs), shape)
    accs = np.reshape(np.asarray(graph_options["accs"]), shape)
    x_ranges = np.reshape(np.asarray(graph_options["x_ranges"]), np.append(shape, 2))
    y_ranges = np.reshape(np.asarray(graph_options["y_ranges"]), np.append(shape, 2))
    t_ranges = np.reshape(np.asarray(graph_options["t_ranges"]), np.append(shape, 2))
    
    times = np.linspace(t_ranges[...,0], t_ranges[...,1], anim_options["frames"], endpoint=False)
    
    figsize = shape * plot_options["figsize-factor"]
    fig, axarr = plt.subplots(*shape, squeeze=False, figsize=figsize)
    
    apply_time = np.vectorize(lambda f, t: lambda x, y: f(x, y, t))
    def animf(i):
        gs = apply_time(funcs, times[i])
        Plot_Wavefunction_2D_Images(gs, x_ranges, y_ranges, accs, shape, axis_options, axarr)
        plt.show()
        
    anim = animation.FuncAnimation(fig, animf, frames=anim_options["frames"])
    anim.save(anim_options["filename"], fps=anim_options["fps"])

In [6]:
# 1D Infinite Square Well
fname = "1D_ISW_Test.mp4"
qn = [1]
coeff = [1]
wavefunc = lambda x, t: ISW_Eigenstate_1D(x, t, 1)
x_range = [0, 1]
t_range = [0, 1]
acc = 0.01
frames = 180
plot_options = {
    "title": "Infinite Square Well",
    "xlabel": r"$x/L$",
    "ylabel": r"$|\Psi|$",
    "colorbar":True
}

anim = Wavefunction_Animation_1D(wavefunc, acc, x_range, t_range, frames, plot_options)
display(anim)
plt.close()

In [7]:
# 2D Infinite Square Well
qn = [(1,1), (2, 2)]
coeff = [1, -1j]
wavefunc = lambda x, y, t: Superpos_2D(ISW_Eigenstate_2D, x, y, t, coeff, qn)
x_range = [0, 1]
y_range = [0, 1]
t_range = [0, ISW_Superpos_2D_Period(qn)]
acc = 1/128
plot_options = {
    "title": r"$\Psi_{1,1} + \Psi_{2,2} + \Psi_{4,4}$",
    "axis-on": True, 
    "xlabel": r"$x/L_x$",
    "ylabel": r"$y/L_y$",
    "colorbar": True,
    "axis-on": False,
    "norm_by_frame": True,
    "figsize-factor": 10
}
anim_options = {
    "filename": "2D_ISW_Period_test.mp4",
    "frames": 60,
    "fps": 30,
    "dpi": 200
}

#Wavefunction_Animation_2D_Image(wavefunc, acc, x_range, y_range, t_range, plot_options, anim_options)

In [8]:
# 1D Free Particle
fname = "1D_Free_Particle_Test.mp4"
sigma = 1
k = 0
wavefunc = lambda x, t: Free_Gaussian_1D(x, t, sigma, k)
x_range = [-10, 10]
t_range = [0, 2*np.pi]
acc = 10/128
frames = 60
plot_options = {
    "title": "1D Free Particle Test", 
    "axis-on": True,
    "xlabel": r"$x$",
    "ylabel": r"$y$",
    "colorbar": True}

anim = Wavefunction_Animation_1D(wavefunc, acc, x_range, t_range, frames, plot_options)
display(anim)
plt.close()

In [9]:
# 2D Free Particle
sigmas = (1, 1)
ks = (1, -1)
wavefunc = lambda x, y, t: Free_Gaussian_2D(x, y, t, sigmas, ks)
x_range = [-10, 10]
y_range = [-10, 10]
t_range = [0, np.pi]
acc = 10/128
frames = 60
plot_options = {
    "title": "1D Free Particle Test",
    "axis-on": True,
    "xlabel": r"$x$",
    "ylabel": r"$y$",
    "colorbar": True,
    "axis-on": False,
    "norm_by_frame": False
}
anim_options = {
    "filename": "2D_Free_Particle_Test.mp4",
    "frames": 1,
    "fps": 30,
    "dpi": 200
}

#Wavefunction_Animation_2D_Image(wavefunc, acc, x_range, y_range, t_range, plot_options, anim_options)

In [10]:
# Free-to-ISW test
fname = "Free-to-ISW_test.mp4"
sigma = 0.5
k = 1
x0 = 0.5
jmax = 1000
freeWave = lambda x, t: Free_Gaussian_1D(x-x0, t, sigma, k)
wavefunc = lambda x, t: Free_to_ISW(x, t, freeWave, jmax)
x_range = [0, 1]
t_range = [0, np.pi/8]
acc = 1/128
frames = 30
plot_options = {"title":"Free Particle to ISW Test", "axis-on":True, "xlabel":r"$x$", "ylabel":r"$y$", "colorbar":True}
#Wavefunction_Animation_1D(wavefunc, acc, x_range, t_range, frames, fname, plot_options)

In [11]:
# 1D Harmonic Oscillator
fname = "1D_HO_Test.mp4"
qn = [0]
coeff = [1]
wavefunc = lambda x, t: HO_Eigenstate_1D(x, t, 0)
x_range = [-5, 5]
t_range = [0, 10]
acc = 0.01
frames = 60
plot_options = {
    "title":"1D Harmonic Oscillator Test",
    "axis-on": True,
    "xlabel": r"$x$",
    "ylabel": r"$y$",
    "colorbar": True
}

anim = Wavefunction_Animation_1D(wavefunc, acc, x_range, t_range, frames, plot_options)
display(anim)
plt.close()

In [ ]:
# 2D Harmonic Oscillator 
quantum_numbers = [(0,0), (1,1)]
coeff = [1, -1j]
x_range = [-5,5]
y_range = x_range
omegas = (1,1)
T = HO_Superpos_2D_Period(quantum_numbers)
print(T)
t_range = [0, T]
acc = 1/256

wavefunc = lambda x, y, t: Superpos_2D(HO_Eigenstate_2D, x, y, t, coeff, quantum_numbers)
plot_options = {
    "title": r"$\Psi_{0,0} + \frac{1}{2^1}\Psi_{1,1} + \frac{1}{2^2}\Psi_{2,2}$",
    "axis-on": True,
    "xlabel": r"$x/x_s$",
    "ylabel": r"$y/y_s$",
    "colorbar": True,
    "axis-on": False,
    "figsize-factor": 5,
    "norm_by_frame": True
}
anim_options = {
    "filename": "2D_HO_period_test.mp4",
    "frames": 60,
    "fps": 30,
    "dpi": 200
}

#Wavefunction_Animation_2D_Image(wavefunc, acc, x_range, y_range, t_range, plot_options, anim_options)

In [38]:
# 1D Harmonic Oscillator Coherent State
fname = "1D_Coherent_State_Test_9.mp4"
alpha = 1
omega = 1
num_components = 9
wavefunc = lambda x, t: HO_Coherent_State_1D(x, t, alpha, omega, num_components)
x_range = [-7, 7]
t_range = [0, 4*np.pi]
acc = 14/128
frames = 60
plot_options = {
    "title": "1D Coherent State Approximation (9 terms)",
    "axis-on": True,
    "xlabel": r"$x/x_s$",
    "ylabel": r"$|\Psi|$",
    "colorbar": True
}

#Wavefunction_Animation_1D(wavefunc, acc, x_range, t_range, frames, fname, plot_options)

In [ ]:
# 2D Harmonic Oscillator Coherent State
alphas = (1, 1j)
num_components = 10
wavefunc = lambda x, y, t: HO_Coherent_State_2D(x, y, t, alphas)
x_range = [-5, 5]
y_range = [-5, 5]
t_range = [0, 2*np.pi]
acc = 5/128
frames = 90
plot_options = {
    "title": "2D Coherent State Test",
    "axis-on": True,
    "xlabel": r"$x/L_x$",
    "ylabel": r"$y/L_y$",
    "colorbar": True,
    "axis-on": False,
    "norm_by_frame": False
}
anim_options = {
    "filename": "2D_Coherent_State_Test.mp4",
    "frames": 90,
    "fps": 30,
    "dpi": 200
}

#Wavefunction_Animation_2D_Image(wavefunc, acc, x_range, y_range, t_range, plot_options, anim_options)

In [ ]:
fname = "1D_double_well_test2.mp4"
acc = 1/128
beta = 2
L = 1
x_range = [-2, 2]
t_range = [0, 2 * np.pi / (odd_energy(beta, L) - even_energy(beta, L))]
wavefunc = lambda x, t: DD_Superpos_1D(x, t, 1, 1, beta, L)
acc = 1/128
frames = 90
plot_options = {"title":r"1D Double Delta-Well ($\beta=2, L=1$)", "axis-on":True, "xlabel":r"$x/L$", "ylabel":r"$|\Psi|$", "colorbar":True}

#Wavefunction_Animation_1D(wavefunc, acc, x_range, t_range, frames, fname, plot_options)

In [ ]:
def make_time_ranges(endpoints, start=0):
    return [(start, x) for x in endpoints]

shape = (2,2)
n = shape[0]*shape[1]

qn00 = [(11,12),(13,11)]
qn01 = [(12,9), (13,12)]
qn10 = [(11,10), (12,12)]
qn11 = [(11,8), (12,13)]
T00 = ISW_Superpos_2D_Period(qn00)
T01 = ISW_Superpos_2D_Period(qn01)
T10 = ISW_Superpos_2D_Period(qn10)
T11 = ISW_Superpos_2D_Period(qn11)

f00 = lambda x,y,t: Superpos_2D(ISW_Eigenstate_2D, x, y ,t, [1,1], qn00)
f01 = lambda x,y,t: Superpos_2D(ISW_Eigenstate_2D, x, y, t, [1,-1j], qn01)
f10 = lambda x,y,t: Superpos_2D(ISW_Eigenstate_2D, x, y, t, [1, 1j], qn10)
f11 = lambda x,y,t: Superpos_2D(ISW_Eigenstate_2D, x, y, t, [1, -1], qn11)
funcs = [f00, f01, f10, f11]
title00 = r"$\Psi_{11,12}+\Psi_{13,11}$"
title01 = r"$\Psi_{12,9}-i\Psi_{13,12}$"
title10 = r"$\Psi_{11,10} + i\Psi_{12,12}$"
title11 = r"$\Psi_{11,8}-\Psi_{12,13}$"


x_ranges = [(0,1)] * n
axis_options = [{'title':title00}, {'title':title01}, {'title':title10}, {'title':title11}]

graph_options = {"accs": [.005] * n,
                 "x_ranges": list(x_ranges),
                 "y_ranges": list(x_ranges),
                 "t_ranges": make_time_ranges([T00, T01, T10, T11])
}
plot_options = {"shape": (2,2),
                "colormap": cm.hsv,
                "figsize-factor": 8,
                "sharex": False,
                "colorbar-on": False,
                "axis-on": False,
                "norm_by_frame": True
}
anim_options = {"frames": 3000,
                "fps": 30,
                "filename": "new_split_test.mp4",
                "dpi": 200
}


#Wavefunction_Animation_2D_Images(funcs, graph_options, plot_options, axis_options, anim_options)

In [ ]:
def get_value_from_hsv_color(color):
    colrange = [0.,1.]
    color = to_rgb(color)
    n = 10000
    r = np.linspace(0,1,n)
    norm = Normalize(0,1)
    mapvals = cmap(np.linspace(0,1,n))[:,:3]
    distance = np.sum((mapvals - color)**2, axis=1)
    return r[np.argmin(distance)]

cmap = cm.hsv
rmap = cmap.reversed()
im = Image.open("cat_256.png")
im.convert('RGB')
rgb_data = np.reshape(np.array(im.getdata())[...,:-1], (*im.size, 3))
mins = np.reshape(rgb_data.min(axis=-1), (*rgb_data.shape[:-1], 1))
alphas = (255 - mins) / 255
shifted_data = rgb_data - mins
scaled_data = (shifted_data / (255 * alphas))
ones = np.ones((*im.size, 1))
scaled_data_with_ones = np.append(scaled_data, ones, axis=-1)
phase_data = 2 * np.pi * np.apply_along_axis(get_value_from_hsv_color, -1, scaled_data_with_ones) - np.pi

complex_vals = np.multiply(alphas.squeeze(), np.exp(1j * phase_data))
rgba_data = np.append(scaled_data, alphas, axis=-1)
plt.imshow(rgba_data)

In [ ]:
acc = 1/im.size[0]
X,Y = np.mgrid[0:1:acc, 0:1:acc]
qn = []
coeff = []
max_n = im.size[0]
for i in range(1, max_n + 1):
    for j in range(1, max_n + 1):
        f = lambda x,y: ISW_Eigenstate_2D(x, y, 0, (i,j))
        prod = f(X,Y) * complex_vals
        coeff.append(prod.sum())
        qn.append((i,j))

In [ ]:
indexed_coeff = sorted(list(zip(qn, coeff)), key=lambda x: x[1], reverse=True)
cutoff = 0.5
skim_coeff = [indexed_coeff.pop()]
norm = sum(np.abs(coeff))
s = np.abs(skim_coeff[0][1])
for i in range(len(indexed_coeff)):
    if s / norm >= cutoff:
        break
    next_coeff = indexed_coeff[i]
    skim_coeff.append(next_coeff)
    s += np.abs(next_coeff[1])

In [ ]:
qn_less, coeff_less = zip(*skim_coeff)
print(len(coeff))
print(len(coeff_less))
print(qn_less[10])
print(coeff_less[10])

In [ ]:
def iterative_2D_superpos(func, x, y, t, coeff, qn):
    norm = 0
    for c in coeff:
        norm += np.abs(c)**2
    norm = np.sqrt(norm)
    res = 0
    for i in range(len(coeff)):
        res = res + coeff[i] * func(x, y, t, qn[i])
    return res / norm

In [ ]:
wavefunc = lambda x, y, t: iterative_2D_superpos(HO_Eigenstate_2D, x, y, t, coeff_less, qn_less)
x_range = [0, 1]
y_range = [0, 1]
t_range = [0, Superpos_Period(HO_Eigenstate_2D_Energy, qn_less)]
print(t_range[1])
acc = 1/im.size[0]
plot_options = {
    "title": r"$\Psi_{cat}$",
    "figsize-factor": 8,
    "axis-on": True, 
    "xlabel": r"$x/L_x$",
    "ylabel": r"$y/L_y$",
    "colorbar": True,
    "axis-on": False,
    "norm_by_frame": True
}
anim_options = {
    "filename": "catwave.mp4",
    "frames": 1,
    "fps": 30,
    "dpi": 200
}

Wavefunction_Animation_2D_Image(wavefunc, acc, x_range, y_range, t_range, plot_options, anim_options)

In [ ]:
xs = [ISW_Eigenstate_2D_Energy(n,m) for n,m in qn]
ys = [np.abs(c) for c in coeff]

plt.figure(figsize=(10,10), dpi=80)
plt.scatter(xs, ys, s=1)
plt.show()